In [ ]:
import kagglehub

# Download latest version
#BASE_PATH = kagglehub.dataset_download(
#    "soumendraprasad/musical-instruments-sound-dataset", 
#)

#print("Path to dataset files:", BASE_PATH)

# couldn't make it download to correct path


Resuming download from 79691776 bytes (5716038602 bytes left)...
Resuming download from https://www.kaggle.com/api/v1/datasets/download/soumendraprasad/musical-instruments-sound-dataset?dataset_version_number=3 (79691776/5795730378) bytes left.


100%|██████████| 5.40G/5.40G [05:42<00:00, 16.7MB/s]  

Extracting files...


Path to dataset files: /home/ivkalu/.cache/kagglehub/datasets/soumendraprasad/musical-instruments-sound-dataset/versions/3


In [8]:

from pedalboard import Pedalboard, Chorus, Reverb, Distortion
from pedalboard.io import AudioFile
import os
from pathlib import Path

import pandas as pd
from IPython.display import Audio

import torch
import torch.nn as nn
import torch.optim as optim
import torchaudio
import os
from torch.utils.data import Dataset, DataLoader
import IPython.display as ipd

In [9]:
BASE_PATH = Path("../data")

In [10]:
def apply_effect(input_folder_path, output_folder_path, file_names, pedalboard):
  for file_name in file_names:
    file_input_path = os.path.join(input_folder_path, file_name)
    output_file_path = os.path.join(output_folder_path, file_name)

    with AudioFile(file_input_path) as f, AudioFile(output_file_path, 'w', f.samplerate, f.num_channels) as o:
      while f.tell() < f.frames:
        chunk = f.read(f.samplerate)
        effected = pedalboard(chunk, f.samplerate, reset=False)
        o.write(effected)

In [ ]:
def display_audio(input_path):
  input_wav, sr = torchaudio.load(input_path)
  print(f"Displaying: {input_path}\nChannels: {input_wav.shape[0]}, Samples {input_wav.shape[1]}")
  display(ipd.Audio(input_path, rate=sr))

In [12]:
csv_path = os.path.join(BASE_PATH, "Metadata_Train.csv")
df = pd.read_csv(csv_path)
guitar_files_only = df[df["Class"] == "Sound_Guitar"]["FileName"]

train_input_folder = os.path.join(BASE_PATH, "Train_submission", "Train_submission")

In [13]:
csv_path = os.path.join(BASE_PATH, "Metadata_Test.csv")
df = pd.read_csv(csv_path)
guitar_files_only_test = df[df["Class"] == "Sound_Guiatr"]["FileName"]

test_input_folder = os.path.join(BASE_PATH, "Test_submission", "Test_submission")

In [23]:
def create_dataset_with_effect(effect_name: str, board: Pedalboard):
    train_output_folder = Path(os.path.join(BASE_PATH, "train_y", effect_name))
    train_output_folder.mkdir(parents=True, exist_ok=True)

    test_output_folder = Path(os.path.join(BASE_PATH, "test_y", effect_name))
    test_output_folder.mkdir(parents=True, exist_ok=True)

    apply_effect(train_input_folder, train_output_folder, guitar_files_only, board)
    apply_effect(test_input_folder, test_output_folder, guitar_files_only_test, board)

    return train_output_folder, test_output_folder

In [24]:
board = Pedalboard([Distortion(drive_db=25)])
train_output_folder, test_output_folder = create_dataset_with_effect("distortion", board)

In [ ]:
board = Pedalboard([Reverb()])
create_dataset_with_effect("reverb", board)

In [25]:
display_audio(os.path.join(train_input_folder, guitar_files_only.iloc[500]))
display_audio(os.path.join(train_output_folder, guitar_files_only.iloc[500]))

Displaying: ../data/Train_submission/Train_submission/LP_E1_muted5.wav
Channels: 1, Samples 408276


Displaying: ../data/train_y/distortion/LP_E1_muted5.wav
Channels: 1, Samples 408276


In [26]:
train_input_files = [os.path.join(train_input_folder, file) for file in guitar_files_only]
train_output_files = [os.path.join(train_output_folder, file) for file in guitar_files_only]

In [45]:
# --- Define the Fully Connected Model ---
class WavDataset(Dataset):
    def __init__(self, input_wav_paths, output_wav_paths, max_length=110250):  # 2.5 sec @ 44.1kHz
        self.input_wav_paths = input_wav_paths
        self.output_wav_paths = output_wav_paths
        self.max_length = max_length

    def __len__(self):
        return len(self.input_wav_paths)

    def __getitem__(self, idx):
        input_wav, sr1 = torchaudio.load(self.input_wav_paths[idx])  # Load non-effected
        output_wav, sr2 = torchaudio.load(self.output_wav_paths[idx])  # Load effected

        assert sr1 == sr2, "Sample rates must match!"

        # Ensure both tensors have the same shape
        input_wav = input_wav.reshape(-1, 1)
        output_wav = output_wav.reshape(-1, 1)

        if self.max_length is not None:
          input_wav = self._pad_or_truncate(input_wav)
          output_wav = self._pad_or_truncate(output_wav)

        return input_wav, output_wav

    def _pad_or_truncate(self, wav_tensor):
        """Pads with zeros or truncates to `max_length`."""
        length = wav_tensor.shape[0]

        if length > self.max_length:
            return wav_tensor[:self.max_length]  # Truncate

        elif length < self.max_length:
            padding = torch.zeros(self.max_length - length, 1)  # Pad with zeros
            return torch.cat((wav_tensor, padding), dim=0)

        return wav_tensor  # Already the correct length


# --- Training Function ---


In [64]:
from baselineFCNet import BaselineFCNet
from trainModel import train_model

dataset = WavDataset(train_input_files, train_output_files)
dataloader = DataLoader(dataset, batch_size=1, shuffle=True)

model = BaselineFCNet(hidden_size=5, hidden_layers=2)
train_model(model, dataloader, epochs=5, lr=0.001, print_batch=False, name="fc_dist")

ImportError: cannot import name 'train_model' from 'trainModel' (/home/ivkalu/Documents/DIPL/src/trainModel.py)

In [33]:
def test_model(model, input_wav_path, output_wav_path):
    model.eval()

    input_wav, sr = torchaudio.load(input_wav_path)
    num_channels = input_wav.shape[0]
    input_samples = input_wav.reshape(-1, 1)

    input_tensor = torch.tensor(input_samples, dtype=torch.float32)

    # Run through the model
    with torch.no_grad():
        output_tensor = model(input_tensor)

    # Reshape back to original format
    output_wav = output_tensor.view(num_channels, -1)

    # Save output WAV file
    torchaudio.save(output_wav_path, output_wav, sample_rate=sr)

model_output_folder = Path(os.path.join(BASE_PATH, "model_output"))
model_output_folder.mkdir(parents=True, exist_ok=True)
file = guitar_files_only_test.iloc[1]
test_model(model, os.path.join(test_input_folder, file), os.path.join(model_output_folder, file))

display_audio(os.path.join(test_input_folder, file))
display_audio(os.path.join(test_output_folder, file))
display_audio(os.path.join(model_output_folder, file))

Displaying: ../data/Test_submission/Test_submission/guitar-chords-70663.wav
Channels: 2, Samples 404352


/tmp/ipykernel_16447/3611731419.py:8: UserWarning: To copy construct from a tensor, it is recommended to use sourceTensor.clone().detach() or sourceTensor.clone().detach().requires_grad_(True), rather than torch.tensor(sourceTensor).
  input_tensor = torch.tensor(input_samples, dtype=torch.float32)


Displaying: ../data/test_y/distortion/guitar-chords-70663.wav
Channels: 2, Samples 404352


Displaying: ../data/model_output/guitar-chords-70663.wav
Channels: 2, Samples 404352


In [ ]:
# TODO
# napravi metrike za mjerit kolko je model dobar, da se kasnije moze lakse usporedit (objektivne metrike)
# provjeri citiranost ddsp i drugo
# dodaj podnaslove i opise za notebook
# probaj razdvojiti u vise pod fileova
# probaj runnat lokalno
# napravit da se izbacuju checkpoint modeli .pkl (ili sta vec